# ニューラル検索の実装 (Amazon SageMaker 編)

## 概要
本ラボでは、テキストクエリを内部的にベクトルに変換してベクトル検索を行うニューラル検索を実装していきます。

ベクトルの生成は、Amazon SageMaker 上にデプロイした密ベクトル埋め込みモデルを利用します。

### 前提事項
本ラボは、[ベクトル検索の実装 (Amazon SageMaker 編)](./vector-search-with-sagemaker.ipynb) を完了していることを前提として作られています。

ベクトル検索の基本的な要素の解説や、ML モデルのデプロイなど、本ラボを実施するにあたって必要な作業も含まれているため、事前に上記のラボを完了させてください。

### ニューラル検索について
ニューラル検索は、OpenSearch に入力されたテキストや画像のクエリデータを、OpenSearch 側でベクトルに変換し、登録と検索を実行する機能です。

一般的なベクトル検索は、クライアント側で用意したベクトルを使用したデータ登録や検索を行う必要があります。従来のテキスト検索に加えてベクトル検索を実装しようとする場合、バックエンド側に埋め込みモデルを呼び出す処理を実装する必要があります。

<img src="./img/dense-vector-embedding-with-backend.png" width="1024">

ニューラル検索では、OpenSearch がバックエンドの責務も担います。OpenSearch はユーザークエリをもとに埋め込みモデルを呼び出し、ベクトルの生成を行います。生成したベクトルは、そのまま格納、ないしはベクトル検索に使用します。

ニューラル検索を活用することで、クライアント側の改修を最小限に抑えつつベクトル検索を導入可能となります。

<img src="./img/dense-vector-embedding-with-connector.png" width="1024">

ニューラル検索は以下のコンポーネントで構成されています

- モデル([リモートモデル][remote-models]): 外部サービス上にホストされた ML モデル。接続を行うためには、コネクターが必要となる。
- [コネクター][connector]: Amazon SageMaker の推論エンドポイントなど、外部エンドポイントへの接続情報を管理するコンポーネント
- Embedding processor: パイプラインから与えられたデータを ML モデルに渡すためのプロセッサ。テキスト埋め込み用の [Text embedding processor][text-embedding]、テキスト+画像のマルチモーダル埋め込み用の [Text/image embedding processor][text-image-embedding] など、元のデータフォーマットによって異なるプロセッサが存在する。
- [Ingest pipelines][ingest-pipelines]: ドキュメント登録時に加工処理を行うパイプライン。1 つ以上のプロセッサで構成されている。Embedding processor を呼び出すことで、ドキュメントのテキストもしくは画像データが格納されたバイナリフィールドからベクトル埋め込みを生成し、元のテキストとベクトルの両方をk-NNインデックスに保存することが可能。
- [Search pipelines][search-pipelines]: 検索クエリもしくは検索結果の加工処理を行うパイプライン。1 つ以上のプロセッサで構成されている。Embedding processor を呼び出すことで、クエリからベクトル埋め込みを生成し、ベクトルフィールドに対する検索を実行することが可能となる。

### コネクター
コネクターは、外部サービスとの連携の大部分を担っています。サービスのエンドポイントや、OpenSearch から渡されたデータを外部サービス向けのリクエストペイロードに書き換えるための定義、外部サービスから受け取った応答を OpenSearch 向けのフォーマットに書き換えるための定義といった情報を保持しています。

### ラボの構成
本ラボでは、ノートブック環境(JupyterLab) および Amazon OpenSearch Service、Amazon SageMaker を使用します。
<img src="./img/architecture-with-sagemaker.png" width="1024">

### 使用するデータセット
本ラボでは、[ベクトル検索の実装 (Amazon SageMaker 編)](./vector-search-with-sagemaker.ipynb) と同様に、[JGLUE][jglue] 内の FAQ データセットである [JSQuAD][jsquad] を使用します。

[remote-models]: https://opensearch.org/docs/latest/ml-commons-plugin/remote-models/index/
[connector]: https://opensearch.org/docs/latest/ml-commons-plugin/remote-models/connectors/
[text-embedding]: https://opensearch.org/docs/latest/ingest-pipelines/processors/text-embedding/
[text-image-embedding]: https://opensearch.org/docs/latest/ingest-pipelines/processors/text-image-embedding/
[ingest-pipelines]: https://opensearch.org/docs/latest/ingest-pipelines/
[search-pipelines]: https://opensearch.org/docs/latest/search-plugins/search-pipelines/index/
[jglue]: https://github.com/yahoojapan/JGLUE/tree/main
[jsquad]: https://github.com/yahoojapan/JGLUE/tree/main/datasets/jsquad-v1.3
[bge-m3]: https://huggingface.co/BAAI/bge-m3


## 事前作業

### パッケージインストール

In [1]:
!pip install opensearch-py requests-aws4auth "awswrangler[opensearch]" --quiet

### インポート

In [2]:
from IPython.core.magic import register_cell_magic
from IPython import get_ipython
import ipywidgets as widgets

import boto3
import json
import time
from datetime import datetime, timedelta
import logging

from functools import lru_cache

import awswrangler as wr
import pandas as pd
import numpy as np
from opensearchpy import OpenSearch, RequestsHttpConnection, AWSV4SignerAuth

import sagemaker
from sagemaker.huggingface import HuggingFaceModel, get_huggingface_llm_image_uri

/opt/conda/lib/python3.12/site-packages/pydantic/_internal/_fields.py:192: UserWarning: Field name "json" in "MonitoringDatasetFormat" shadows an attribute in parent "Base"
  warnings.warn(


sagemaker.config INFO - Not applying SDK defaults from location: /etc/xdg/sagemaker/config.yaml
sagemaker.config INFO - Not applying SDK defaults from location: /home/sagemaker-user/.config/sagemaker/config.yaml


### ヘルパー関数の定義
以降の処理を実行する際に必要なヘルパー関数を定義しておきます。

In [3]:
def search_cloudformation_output(stackname, key):
    cloudformation_client = boto3.client("cloudformation", region_name=default_region)
    for output in cloudformation_client.describe_stacks(StackName=stackname)["Stacks"][0]["Outputs"]:
        if output["OutputKey"] == key:
            return output["OutputValue"]
    raise ValueError(f"{key} is not found in outputs of {stackname}.")

def search_sagemaker_inference_endpoint(endpoint_name, region):
    sagemaker_client = boto3.client("sagemaker", region_name=region)
    try:
        response = sagemaker_client.search(
            Resource="Endpoint",
            SearchExpression={
                "Filters": [
                    {
                        "Name": "EndpointName",
                        "Operator": "Contains",
                        "Value": endpoint_name
                    },
                ],
            },
            SortBy="LastModifiedTime",
            SortOrder="Descending"
        )
        return response["Results"]
    except Exception as e:
        print(e)

### 共通変数のセット

In [4]:
default_region = boto3.Session().region_name
logging.getLogger().setLevel(logging.ERROR)

## リソース作成

### Amazon SageMaker 関連リソースの作成

### Amazon SageMaker 推論エンドポイント情報の取得
[ベクトル検索の実装 (Amazon SageMaker 編)](./vector-search-with-sagemaker.ipynb) で作成したエンドポイントの情報を取得します。

In [5]:
try:
    sagemaker_region = default_region
    embedding_model_id_on_hf = "BAAI/bge-m3"
    embedding_model_name = embedding_model_id_on_hf.lower().replace("/", "-")

    embedding_endpoint_name_prefix = embedding_model_name
    embedding_endpoints = search_sagemaker_inference_endpoint(embedding_endpoint_name_prefix, sagemaker_region)

    if len(embedding_endpoints) == 0:
        raise ValueError(f"Endpoint of model for {embedding_model_id_on_hf} is not found. Please deploy the model.")
    else:
        print(f"Endpoint of model for {embedding_model_id_on_hf} is found.")
    
except Exception as e:
    print(e)

Endpoint of model for BAAI/bge-m3 is found.


#### エンドポイントの選択
エンドポイントが複数存在する場合は、ドロップダウンメニューからどのエンドポイントを参照するかを選択可能です。

In [6]:
embedding_endpoint_dropdown_options = []
for embedding_endpoint in embedding_endpoints:
    embedding_endpoint_name = embedding_endpoint["Endpoint"]["EndpointName"]
    embedding_endpoint_dropdown_options.append(embedding_endpoint_name)

embedding_endpoint_name_dropdown = widgets.Dropdown(
    options=embedding_endpoint_dropdown_options,
    description='endpoint'
)
embedding_endpoint_name_dropdown

Dropdown(description='endpoint', options=('baai-bge-m3-instance-2025-04-14-05-40-48-158',), value='baai-bge-m3…

In [7]:
embedding_endpoint_name = embedding_endpoint_name_dropdown.value

embedding_endpoint_url = f"https://runtime.sagemaker.{default_region}.amazonaws.com/endpoints/{embedding_endpoint_name}/invocations"
print(f"\nendpoint name: {embedding_endpoint_name}")
print(f"endpoint url: {embedding_endpoint_url}")


endpoint name: baai-bge-m3-instance-2025-04-14-05-40-48-158
endpoint url: https://runtime.sagemaker.us-west-2.amazonaws.com/endpoints/baai-bge-m3-instance-2025-04-14-05-40-48-158/invocations


#### 推論エンドポイントのテスト呼び出し
選択したエンドポイントに対して推論を実行し、ベクトルが取得できることを確認します

In [8]:
%%time

payload = {
    "inputs": [
        "hello world"
    ]
}
body = bytes(json.dumps(payload), 'utf-8')

sagemaker_runtime_client = boto3.client("sagemaker-runtime", region_name=sagemaker_region)
response = sagemaker_runtime_client.invoke_endpoint(
    EndpointName=embedding_endpoint_name,
    ContentType="application/json",
    Accept="application/json",
    Body=body
)

embeddings = eval(response['Body'].read().decode('utf-8'))

print("embedding:")
print(np.array(embeddings[0]))
print("dimension:")
print(np.shape(embeddings[0]))


embedding:
[-0.04022236  0.03693659 -0.02904319 ...  0.02645612 -0.03298989
  0.01630611]
dimension:
(1024,)
CPU times: user 16.2 ms, sys: 3.58 ms, total: 19.8 ms
Wall time: 70.8 ms


### サンプルデータの読み込み
サンプルデータをダウンロードし、Pandas の DataFrame 形式に変換します

In [9]:
%%time
dataset_dir = "./dataset/jsquad/"
%mkdir -p $dataset_dir
!curl -L -s -o $dataset_dir/valid.json https://github.com/yahoojapan/JGLUE/raw/main/datasets/jsquad-v1.3/valid-v1.3.json 
#!curl -L -s -o $dataset_dir/train.json https://github.com/yahoojapan/JGLUE/raw/main/datasets/jsquad-v1.3/train-v1.3.json 

CPU times: user 12.7 ms, sys: 16.1 ms, total: 28.8 ms
Wall time: 1.24 s


In [10]:
%%time
import pandas as pd
import json

def squad_json_to_dataframe(input_file_path, record_path=["data", "paragraphs", "qas", "answers"]):
    file = json.loads(open(input_file_path).read())
    m = pd.json_normalize(file, record_path[:-1])
    r = pd.json_normalize(file, record_path[:-2])

    idx = np.repeat(r["context"].values, r.qas.str.len())
    m["context"] = idx
    m["answers"] = m["answers"]
    m["answers"] = m["answers"].apply(lambda x: np.unique(pd.json_normalize(x)["text"].to_list()))
    return m[["id", "question", "context", "answers"]]

valid_filename = f"{dataset_dir}/valid.json"
valid_df = squad_json_to_dataframe(valid_filename)

#train_filename = f"{dataset_dir}/train.json"
#train_df = squad_json_to_dataframe(train_filename)



CPU times: user 1.56 s, sys: 49.1 ms, total: 1.61 s
Wall time: 1.59 s


### サンプルデータの確認
サンプルデータは質問文フィールドの question、回答の answers、説明文の context フィールド、問題 ID である id フィールドから構成されています。

サンプルデータの一部を見ていきましょう。

In [11]:
valid_df

id                        question  \
0     a10336p0q0              日本で梅雨がないのは北海道とどこか。   
1     a10336p0q1                     梅雨とは何季の一種か?   
2     a10336p0q2        梅雨は、世界的にどのあたりで見られる気象ですか？   
3     a10336p0q3                  梅雨がみられるのはどの期間？   
4     a10336p1q0                    入梅は何の目安の時期か？   
...          ...                             ...   
4437  a95156p5q3  国際銀行間通信協会ならびに国際決済機関の何と何も企業体である   
4438  a95156p6q0                  ゼネコンはどの国特有の形態か   
4439  a95156p6q1    多国籍企業においてゼネコンはどこの国特有の形態であるか？   
4440  a95156p6q2                     多国籍企業を一つ挙げよ   
4441  a95156p6q3                ゼネコンはどの国の特有の形態か？   

                                                context  \
0     梅雨 [SEP] 梅雨（つゆ、ばいう）は、北海道と小笠原諸島を除く日本、朝鮮半島南部、中国の...   
1     梅雨 [SEP] 梅雨（つゆ、ばいう）は、北海道と小笠原諸島を除く日本、朝鮮半島南部、中国の...   
2     梅雨 [SEP] 梅雨（つゆ、ばいう）は、北海道と小笠原諸島を除く日本、朝鮮半島南部、中国の...   
3     梅雨 [SEP] 梅雨（つゆ、ばいう）は、北海道と小笠原諸島を除く日本、朝鮮半島南部、中国の...   
4     梅雨 [SEP] 梅雨の時期が始まることを梅雨入りや入梅（にゅうばい）といい、社会通念上・気...   
...                                                 ...   
4437  多国籍企業 [SEP] 国際銀行間通信協会ならびに国際決済機関のクリアストリームとユーロクリ...   
4438  多国籍企業 [SEP] ゼネコンは日本特有の形態。セメントメジャーにラファージュホルシムやイ...   
4439  多国籍企業 [SEP] ゼネコンは日本特有の形態。セメントメジャーにラファージュホルシムやイ...   
4440  多国籍企業 [SEP] ゼネコンは日本特有の形態。セメントメジャーにラファージュホルシムやイ...   
4441  多国籍企業 [SEP] ゼネコンは日本特有の形態。セメントメジャーにラファージュホルシムやイ...   

                                         answers  
0                            [小笠原諸島, 小笠原諸島を除く日本]  
1                                           [雨季]  
2                               [東アジア, 東アジアの広範囲]  
3                           [5月から7月, 5月から7月にかけて]  
4     [春の終わりであるとともに夏の始まり（初夏）, 田植えの時期, 田植えの時期の目安]  
...                                          ...  
4437                           [クリアストリームとユーロクリア]  
4438                                        [日本]  
4439                                        [日本]  
4440                     [イタルチェメンティ, ラファージュホルシム]  
4441                                        [日本]  

[4442 rows x 4 columns]

### OpenSearch 関連リソースの作成

#### OpenSearch クライアントの作成
ドメイン(クラスター)に接続するためのエンドポイント情報を CloudFormation スタックの出力から取得し、OpenSearch クライアントを作成します。

In [12]:
cloudformation_stack_name = "search-lab-jp"
opensearch_cluster_endpoint = search_cloudformation_output(cloudformation_stack_name, "OpenSearchDomainEndpoint")

credentials = boto3.Session().get_credentials()
service_code = "es"
auth = AWSV4SignerAuth(credentials=credentials, region=default_region, service=service_code)
opensearch_client = OpenSearch(
    hosts=[{"host": opensearch_cluster_endpoint, "port": 443}],
    http_compress=True, 
    http_auth=auth,
    use_ssl=True,
    verify_certs=True,
    connection_class = RequestsHttpConnection
)
opensearch_client

<OpenSearch([{'host': 'vpc-opensearchservi-cyiiwlmtgk2r-jkahtzltl6zkpgjx5czbxq5vvy.us-west-2.es.amazonaws.com', 'port': 443}])>

OpenSearch クラスターへのネットワーク接続性が確保されており、OpenSearch の Security 機能により API リクエストが許可されているかを確認します。
レスポンスに cluster_name や cluster_uuid が含まれていれば、接続確認が無事完了したと判断できます

In [13]:
opensearch_client.info()

{'name': 'cf756e86f83b28e0bd2ffe2ff501ccf4',
 'cluster_name': '123456789012:opensearchservi-cyiiwlmtgk2r',
 'cluster_uuid': 'UoIf1GJCTauJlwbKQrxTUA',
 'version': {'distribution': 'opensearch',
  'number': '2.17.0',
  'build_type': 'tar',
  'build_hash': 'unknown',
  'build_date': '2025-02-14T09:38:50.023788640Z',
  'build_snapshot': False,
  'lucene_version': '9.11.1',
  'minimum_wire_compatibility_version': '7.10.0',
  'minimum_index_compatibility_version': '7.0.0'},
 'tagline': 'The OpenSearch Project: https://opensearch.org/'}

#### インデックスの作成
id、question、context、answers フィールドを格納するための文字列型フィールドに加えて、question、context フィールドから生成したベクトルデータを格納するための context_dense_embedding、question_sparse_embedding フィールドを持つインデックスを作成します。

文字列型フィールドについては、テキスト検索でもある程度の検索精度を出せるように、id フィールドを除いて sudachi のカスタムアナライザーをセットしています。

In [14]:
payload = {
  "mappings": {
    "properties": {
      "id": {"type": "keyword"},
      "question": {"type": "text", "analyzer": "custom_sudachi_analyzer"},
      "context":  {"type": "text", "analyzer": "custom_sudachi_analyzer"},
      "answers":  {"type": "text", "analyzer": "custom_sudachi_analyzer"},
      "question_embedding": {
        "type": "knn_vector",
        "dimension": 1024,
        "space_type": "l2",
        "method": {
          "name": "hnsw",
          "engine": "faiss",
        }
      },
      "context_embedding": {
        "type": "knn_vector",
        "dimension": 1024,
        "space_type": "l2",
        "method": {
          "name": "hnsw",
          "engine": "faiss",
        },
      }
    }
  },
  "settings": {
    "index.knn": True,
    "index.number_of_shards": 1,
    "index.number_of_replicas": 0,
    "analysis": {
      "analyzer": {
        "custom_sudachi_analyzer": {
          "char_filter": ["icu_normalizer"],
          "filter": [
              "sudachi_normalizedform",
              "custom_sudachi_part_of_speech"
          ],
          "tokenizer": "sudachi_tokenizer",
          "type": "custom"
        }
      },
      "filter": {
        "custom_sudachi_part_of_speech": {
          "type": "sudachi_part_of_speech",
          "stoptags": ["感動詞,フィラー","接頭辞","代名詞","副詞","助詞","助動詞","動詞,一般,*,*,*,終止形-一般","名詞,普通名詞,副詞可能"]
        }
      }
    }
  }
}
# インデックス名を指定
index_name = "jsquad-neural-search"

try:
    # 既に同名のインデックスが存在する場合、いったん削除を行う
    print("# delete index")
    response = opensearch_client.indices.delete(index=index_name)
    print(json.dumps(response, indent=2))
except Exception as e:
    print(e)

# インデックスを作成
response = opensearch_client.indices.create(index_name, body=payload)
response

# delete index
NotFoundError(404, 'index_not_found_exception', 'no such index [jsquad-neural-search]', jsquad-neural-search, index_or_alias)


{'acknowledged': True,
 'shards_acknowledged': True,
 'index': 'jsquad-neural-search'}

#### OpenSearch へのモデル登録
SageMaker 上にデプロイしたモデルを呼び出すためのコンポーネントを作成します。

モデルは、コネクタと呼ばれる外部接続を定義したコンポーネントで構成されています。
今回の構成では、モデルは Text Embedding Processor と呼ばれる、入力テキストをベクトルに変換するためのプロセッサーから呼び出されます。




##### Amazon SageMaker のモデル情報・エンドポイント情報の確認
本セルの実行でエラーが発生する場合は、再度 SageMaker 上でのモデルデプロイをお試しください。

In [15]:
print(f"model name: {embedding_model_name}")
print(f"endpoint name: {embedding_endpoint_name}")
print(f"endpoint url: {embedding_endpoint_url}")

model name: baai-bge-m3
endpoint name: baai-bge-m3-instance-2025-04-14-05-40-48-158
endpoint url: https://runtime.sagemaker.us-west-2.amazonaws.com/endpoints/baai-bge-m3-instance-2025-04-14-05-40-48-158/invocations


##### コネクタ用 IAM Role ARN の確認
OpenSearch コネクタから AWS サービスに接続する際、任意の IAM ロールの権限を引き受ける必要があります。引受対象の IAM ロールを CloudFormation スタックの出力から取得します。

In [16]:
cloudformation_stack_name = "search-lab-jp"
opensearch_connector_role_arn = search_cloudformation_output(cloudformation_stack_name, 'OpenSearchConnectorRoleArn')
opensearch_connector_role_arn

'arn:aws:iam::123456789012:role/workshop/search-lab-jp/search-lab-jp-OpenSearchConnectorRole-YuvZq1QfVLWw'

##### コネクタの作成
Amazon SageMaker 上のモデルを呼び出す定義を記載したコネクタを作成します。
コネクタは、OpenSearch におけるモデルの一要素です。

コネクタの処理の流れは以下の通りです。

1. pre_process_function の定義を元に、OpenSearch の Ingestion pipeline もしくは Search pipline 内の Text embeddding processor から与えられた入力から、推論エンドポイントに与えるパラメーターを作成
1. pre_process_function によって変換されたパラメーターを元に、request_body の定義に沿ってペイロードを組み立て、推論エンドポイントの呼び出しを行う
1. post_process_function の定義を元に、推論エンドポイントから返却された推論結果を加工し、Text embedding processor に返却


In [17]:
payload = {
  "name": embedding_model_name, 
  "description": "Remote connector for " + embedding_model_name,
  "version": 1, 
  "protocol": "aws_sigv4",
  "credential": {
    "roleArn": opensearch_connector_role_arn
  },
  "parameters": {
    "region": sagemaker_region,
    "service_name": "sagemaker"
  },
  "actions": [
    {
      "action_type": "predict",
      "method": "POST",
      "headers": {"content-type": "application/json"},
      "url": embedding_endpoint_url,
      "pre_process_function": """
        StringBuilder builder = new StringBuilder();
        builder.append("\\"");
        builder.append(params.text_docs[0]);
        builder.append("\\"");
        def parameters = "{" +"\\"inputs\\":" + builder + "}";
        return "{" +"\\"parameters\\":" + parameters + "}";
        """,
      "request_body": "{\"inputs\": \"${parameters.inputs}\"}",
      "post_process_function": "connector.post_process.default.embedding"
    }
  ]
}

# API の実行
response = opensearch_client.http.post("/_plugins/_ml/connectors/_create", body=payload)

# 結果からコネクタ ID を取得
opensearch_embedding_connector_id = response["connector_id"]
print("embedding connector id: " + opensearch_embedding_connector_id)

embedding connector id: XBXhMpYBDSxiOaui0yx5


##### OpenSearch へのモデル登録
コネクタを元に、OpenSearch にモデル情報を登録します。

In [18]:
payload = {
    "name": embedding_model_name,
    "description": embedding_model_name,
    "function_name": "remote",
    "connector_id": opensearch_embedding_connector_id
}
response = opensearch_client.http.post("/_plugins/_ml/models/_register?deploy=true", body=payload)

opensearch_embedding_model_id = response['model_id']

for i in range(300):
    ml_model_status = opensearch_client.http.get("/_plugins/_ml/models/"+ opensearch_embedding_model_id)
    model_state = ml_model_status.get("model_state")
    if model_state in ["DEPLOYED", "PARTIALLY_DEPLOYED"]:
        break
    time.sleep(1)

if model_state == "DEPLOYED":
    print("embedding model " + opensearch_embedding_model_id + " is deployed successfully")
elif model_state == "PARTIALLY_DEPLOYED":
    print("embedding model " + opensearch_embedding_model_id + " is deployed only partially")
else:
    raise Exception("embedding model " + opensearch_embedding_model_id + " deployment failed")

print(ml_model_status)

embedding model XxXhMpYBDSxiOaui0yy5 is deployed successfully
{'name': 'baai-bge-m3', 'model_group_id': 'XRXhMpYBDSxiOaui0yyb', 'algorithm': 'REMOTE', 'model_version': '1', 'description': 'baai-bge-m3', 'model_state': 'DEPLOYED', 'created_time': 1744610382777, 'last_updated_time': 1744610382886, 'last_deployed_time': 1744610382886, 'auto_redeploy_retry_times': 0, 'planning_worker_node_count': 1, 'current_worker_node_count': 1, 'planning_worker_nodes': ['egO7SuqlQrO2lfG5nvousQ'], 'deploy_to_all_nodes': True, 'is_hidden': False, 'connector_id': 'XBXhMpYBDSxiOaui0yx5'}


#### モデルの呼び出しテスト
OpenSearch 経由で Amazon SageMaker 上の埋め込みモデルを実行できることを確認します。モデルの呼び出し方は 2 パターンあります。

##### Text embedding processor からの呼び出しを想定したテストパターン
Text embedding processor からの呼び出しを想定する場合は、以下パスの API を使用します。
Text embedding processor が text_embedding モデルを呼び出す際のパラメーターキーは text_docs で固定されています。同パラメーターには、クライアントからの入力テキストがセットされています。

In [19]:
path = "/_plugins/_ml/_predict/text_embedding/" + opensearch_embedding_model_id
payload = {
  "text_docs": ["日本で梅雨がないのはどこ？"]
}
response = opensearch_client.http.post(path, body=payload)
response

{'inference_results': [{'output': [{'name': 'sentence_embedding',
     'data_type': 'FLOAT32',
     'shape': [1024],
     'data': [-0.038697254,
      0.03304789,
      -0.015738808,
      -0.04927402,
      0.0051981383,
      -0.021550614,
      -0.005870467,
      0.027037539,
      -0.028571712,
      -0.020106688,
      -0.0024163222,
      -0.023788702,
      0.004117449,
      0.0018996669,
      0.0103421295,
      -0.0035173167,
      0.018554466,
      0.0049183774,
      0.0056629023,
      0.004692764,
      0.013572916,
      -0.0129772965,
      -0.034690354,
      -0.059670296,
      0.040754847,
      -0.004801058,
      -0.04790229,
      0.029040989,
      -0.017652012,
      0.005026672,
      0.0028923668,
      0.0146468375,
      -0.042379268,
      -0.015558317,
      -0.0066059674,
      0.0051485035,
      -0.00407007,
      -0.046169575,
      -0.031026388,
      -0.0139970705,
      0.07891063,
      -0.014150488,
      0.023915047,
      0.0038151266,
      

##### pre_process_function をバイパスするパターン
ML モデル配下の predict API を直接呼び出してテストを行うことも可能です。この場合 pre_process_function は呼び出されず、parameters に記載した値が直接コネクタで指定した推論エンドポイントに渡されます。


In [20]:
path = "/_plugins/_ml/models/" + opensearch_embedding_model_id + "/_predict"
payload = {
  "parameters": {
    "inputs": "日本で梅雨がないのはどこ？"
  }
}
response = opensearch_client.http.post(path, body=payload)
response

{'inference_results': [{'output': [{'name': 'sentence_embedding',
     'data_type': 'FLOAT32',
     'shape': [1024],
     'data': [-0.038697254,
      0.03304789,
      -0.015738808,
      -0.04927402,
      0.0051981383,
      -0.021550614,
      -0.005870467,
      0.027037539,
      -0.028571712,
      -0.020106688,
      -0.0024163222,
      -0.023788702,
      0.004117449,
      0.0018996669,
      0.0103421295,
      -0.0035173167,
      0.018554466,
      0.0049183774,
      0.0056629023,
      0.004692764,
      0.013572916,
      -0.0129772965,
      -0.034690354,
      -0.059670296,
      0.040754847,
      -0.004801058,
      -0.04790229,
      0.029040989,
      -0.017652012,
      0.005026672,
      0.0028923668,
      0.0146468375,
      -0.042379268,
      -0.015558317,
      -0.0066059674,
      0.0051485035,
      -0.00407007,
      -0.046169575,
      -0.031026388,
      -0.0139970705,
      0.07891063,
      -0.014150488,
      0.023915047,
      0.0038151266,
      

#### Ingestion pipeline の作成
データ登録時にベクトル埋め込みを行う Ingestion pipeline を作成します。埋め込み元のデータはテキストであるため、今回は [Text embedding processor](https://opensearch.org/docs/latest/ingest-pipelines/processors/text-embedding/) を使用します。

Text embedding processor では、埋め込みの元となるフィールドと埋め込みを格納するフィールドのマッピングを field_map 内で定義し、model_id には埋め込みに用いるモデル ID を指定します。

以下は Ingestion pipeline による埋め込みのイメージです

<img src="./img/neural-search-ingestion.png">

In [21]:
payload = {
  "processors": [
    {
      "text_embedding": {
        "model_id": opensearch_embedding_model_id,
        "field_map": {
            "question": "question_embedding",
            "context": "context_embedding"
        }
      }
    }
  ]
}

ingestion_pipeline_id = f"{embedding_model_name}_neural_search_ingestion"

response = opensearch_client.http.put("/_ingest/pipeline/" + ingestion_pipeline_id, body=payload)
print(response)

response = opensearch_client.http.get("/_ingest/pipeline/" + ingestion_pipeline_id)
print(response)


{'acknowledged': True}
{'baai-bge-m3_neural_search_ingestion': {'processors': [{'text_embedding': {'model_id': 'XxXhMpYBDSxiOaui0yy5', 'field_map': {'question': 'question_embedding', 'context': 'context_embedding'}}}]}}


作成したパイプラインは _simulate API でテストが可能です。 context_embedding および question_embedding フィールドが含まれていれば正常にパイプラインが動作していると判断できます。

In [22]:
%%time
payload = {
  "docs": [
    {
      "_index": "testindex1",
      "_id": "1",
      "_source":{
         "question": "日本で梅雨がないのはどこか。",
         "context": "梅雨 [SEP] 梅雨（つゆ、ばいう）は、北海道と小笠原諸島を除く日本、朝鮮半島南部、中国の南部から長江流域にかけての沿海部、および台湾など、東アジアの広範囲においてみられる特有の気象現象で、5月から7月にかけて来る曇りや雨の多い期間のこと。雨季の一種である。 ",
      }
    }
  ]
}
response = opensearch_client.http.post("/_ingest/pipeline/" + ingestion_pipeline_id + "/_simulate", body=payload)
print(response)

{'docs': [{'doc': {'_index': 'testindex1', '_id': '1', '_source': {'context': '梅雨 [SEP] 梅雨（つゆ、ばいう）は、北海道と小笠原諸島を除く日本、朝鮮半島南部、中国の南部から長江流域にかけての沿海部、および台湾など、東アジアの広範囲においてみられる特有の気象現象で、5月から7月にかけて来る曇りや雨の多い期間のこと。雨季の一種である。 ', 'context_embedding': [-0.006070981, 0.0046303687, -0.054263838, -0.017420249, -0.011021749, -0.022005524, -0.046972968, 0.04480849, -0.014610225, 0.0092322575, -0.029315384, -0.026429413, 0.015834864, 0.0025252241, -0.0024077443, 0.003951596, 0.04287185, 0.03410002, 0.002191771, -0.00326333, 0.04158076, 0.013043827, -0.019261954, -0.032751966, -0.03007485, -0.028233144, -0.036435377, 0.020942273, 0.023277631, 0.03330258, 0.0046517286, 0.04837798, 0.04469457, 0.0068874066, -0.019898007, -0.010300256, -0.044086996, -0.028517945, -0.011391989, 0.037232816, 0.047504593, -0.026733201, 0.034062047, -0.009460097, 0.002223811, -0.020372674, -0.04378321, -0.032486156, -0.0087101245, -0.031688716, -0.029315384, -0.032865886, 0.06440271, -0.04355537, -0.008472792, 0.020429634, 0.03045458

#### Search pipeline の作成
クライアントから入力されたテキストベースのクエリをベクトルベースのクエリに変換するための Search pipeline を作成します。

Search pipeline は、検索時のクエリ書き換え用の Request processors、レスポンス書き換え用の Response processors、スコアなどの検索結果を書き換える Search phase results processors の 3 タイプが存在します。

<img src='./img/search-pipelines.png'>

今回使用する [Neural query enricher processor][neural-query-enricher] は Request processors に属しています。このプロセッサは、後述する Neural query を実行する際のデフォルトモデルをセットするものです。

[search-request-processors]: https://opensearch.org/docs/latest/search-plugins/search-pipelines/search-processors/#search-request-processors
[search-response-processors]: https://opensearch.org/docs/latest/search-plugins/search-pipelines/search-processors/#search-response-processors
[search-phase-results-processors]: https://opensearch.org/docs/latest/search-plugins/search-pipelines/search-processors/#search-phase-results-processors
[neural-query-enricher]: https://opensearch.org/docs/latest/search-plugins/search-pipelines/neural-query-enricher/

In [23]:
payload={
  "request_processors": [
    {
      "neural_query_enricher" : {
        "default_model_id": opensearch_embedding_model_id
      }
    }
  ]
}
# パイプライン ID の指定
search_pipeline_id = f"{embedding_model_name}_neural_search_query"
# パイプライン作成 API の呼び出し
response = opensearch_client.http.put("/_search/pipeline/" + search_pipeline_id, body=payload)
print(response)

response = opensearch_client.http.get("/_search/pipeline/" + search_pipeline_id)
print(response)


{'acknowledged': True}
{'baai-bge-m3_neural_search_query': {'request_processors': [{'neural_query_enricher': {'default_model_id': 'XxXhMpYBDSxiOaui0yy5'}}]}}


Search pipeline についてはテスト用の API が提供されていないため、実際に Neural search を実行して動作を確認していきます。

## ニューラル検索の実行
データセットを OpenSearch にロードし、検索を実行していきます。


### データロード
DataFrame 形式に変換したサンプルデータセットを OpenSearch に登録していきます。DataFrame にはベクトルデータは含まれていませんが、Ingestion pipeline を通じてデータを登録することでベクトルデータが OpenSearch 側で生成・登録されます。

In [24]:
%%time
index_name = "jsquad-neural-search"
response = wr.opensearch.index_df(
    client=opensearch_client,
    df=valid_df,
    use_threads=True,
    id_keys=["id"],
    index=index_name,
    bulk_size=10, # 10 件ずつ書き込み
    refresh=False,
    pipeline=ingestion_pipeline_id
)

CPU times: user 1.92 s, sys: 501 ms, total: 2.42 s
Wall time: 37 s


response["success"] の値が DataFrame の件数と一致しているかを確認します。True が表示される場合は全件登録に成功していると判断できます。

In [25]:
response["success"] == valid_df["id"].count()

True

本ラボではデータ登録時に意図的に Refresh オプションを無効化しているため、念のため Refresh API を実行し、登録されたドキュメントが確実に検索可能となるようにします

In [26]:
index_name = "jsquad-neural-search"
response = opensearch_client.indices.refresh(index_name)
response = opensearch_client.indices.forcemerge(index_name, max_num_segments=1)

パイプラインを通して登録されたドキュメントにベクトルデータが登録されていることを確認します。
**_source.question_embedding** および **_source.context_embedding** フィールドに数値配列が格納されていれば、パイプラインによる埋め込み生成とベクトルデータの格納が正常に行われたと判断することができます。

In [27]:
%%time
index_name = "jsquad-neural-search"
payload = {
  "size": 10,
  "query": {
    "match_all": {}
  },
}
# 検索 API を実行
response = opensearch_client.search(
    body = payload,
    index = index_name,
    filter_path = "hits.hits"
)

# 結果を表示
pd.json_normalize(response["hits"]["hits"])

CPU times: user 9.99 ms, sys: 0 ns, total: 9.99 ms
Wall time: 35.2 ms


_index          _id  _score  \
0  jsquad-neural-search   a10336p0q0     1.0   
1  jsquad-neural-search   a10336p0q1     1.0   
2  jsquad-neural-search   a10336p0q2     1.0   
3  jsquad-neural-search   a10336p0q3     1.0   
4  jsquad-neural-search   a10336p1q0     1.0   
5  jsquad-neural-search   a10336p1q1     1.0   
6  jsquad-neural-search  a10336p10q0     1.0   
7  jsquad-neural-search  a10336p10q1     1.0   
8  jsquad-neural-search  a10336p10q2     1.0   
9  jsquad-neural-search  a10336p10q3     1.0   

                       _source.question  \
0                    日本で梅雨がないのは北海道とどこか。   
1                           梅雨とは何季の一種か?   
2              梅雨は、世界的にどのあたりで見られる気象ですか？   
3                        梅雨がみられるのはどの期間？   
4                          入梅は何の目安の時期か？   
5                        梅雨明けの別名を何というか。   
6      シベリアから中国大陸にかけての広範囲を冷たく乾燥させる気団は？7   
7               冬の間、シベリア気団が覆っている範囲はどこか？   
8      冬の間、シベリアから中国大陸にかけての広範囲を覆うものは何気団か   
9  冬の間、シベリアから中国大陸にかけての広範囲を覆う冷たく乾燥した気団は?   

                          _source.question_embedding  \
0  [-0.02515889, 0.011687988, -0.024402501, -0.03...   
1  [-0.032506354, 0.005247642, -0.027506817, -0.0...   
2  [-0.017776996, 0.024720104, -0.03772077, -0.00...   
3  [-0.041788705, 0.019765943, -0.036015015, -0.0...   
4  [-0.010982876, 0.039066855, -0.03545579, -8.36...   
5  [-0.007968731, 0.045498587, -0.059529476, -0.0...   
6  [-0.0103905825, 0.03669786, -0.04044406, 0.011...   
7  [-0.042147983, 0.007449045, -0.036018375, 0.01...   
8  [-0.03716481, 0.0053374995, -0.035008244, 0.01...   
9  [-0.021425376, 0.0131031955, -0.043457296, 0.0...   

                                     _source.context  \
0  梅雨 [SEP] 梅雨（つゆ、ばいう）は、北海道と小笠原諸島を除く日本、朝鮮半島南部、中国の...   
1  梅雨 [SEP] 梅雨（つゆ、ばいう）は、北海道と小笠原諸島を除く日本、朝鮮半島南部、中国の...   
2  梅雨 [SEP] 梅雨（つゆ、ばいう）は、北海道と小笠原諸島を除く日本、朝鮮半島南部、中国の...   
3  梅雨 [SEP] 梅雨（つゆ、ばいう）は、北海道と小笠原諸島を除く日本、朝鮮半島南部、中国の...   
4  梅雨 [SEP] 梅雨の時期が始まることを梅雨入りや入梅（にゅうばい）といい、社会通念上・気...   
5  梅雨 [SEP] 梅雨の時期が始まることを梅雨入りや入梅（にゅうばい）といい、社会通念上・気...   
6  梅雨 [SEP] 冬の間、シベリアから中国大陸にかけての広範囲を冷たく乾燥したシベリア気団が...   
7  梅雨 [SEP] 冬の間、シベリアから中国大陸にかけての広範囲を冷たく乾燥したシベリア気団が...   
8  梅雨 [SEP] 冬の間、シベリアから中国大陸にかけての広範囲を冷たく乾燥したシベリア気団が...   
9  梅雨 [SEP] 冬の間、シベリアから中国大陸にかけての広範囲を冷たく乾燥したシベリア気団が...   

                              _source.answers   _source.id  \
0                         [小笠原諸島, 小笠原諸島を除く日本]   a10336p0q0   
1                                        [雨季]   a10336p0q1   
2                            [東アジア, 東アジアの広範囲]   a10336p0q2   
3                        [5月から7月, 5月から7月にかけて]   a10336p0q3   
4  [春の終わりであるとともに夏の始まり（初夏）, 田植えの時期, 田植えの時期の目安]   a10336p1q0   
5                             [出梅, 出梅（しゅつばい）]   a10336p1q1   
6                                    [シベリア気団]  a10336p10q0   
7                [シベリアから中国大陸, シベリアから中国大陸にかけて]  a10336p10q1   
8                                    [シベリア気団]  a10336p10q2   
9                                    [シベリア気団]  a10336p10q3   

                           _source.context_embedding  
0  [-0.0050909766, 0.0050436184, -0.053343963, -0...  
1  [-0.0050909766, 0.0050436184, -0.053343963, -0...  
2  [-0.0050909766, 0.0050436184, -0.053343963, -0...  
3  [-0.0050909766, 0.0050436184, -0.053343963, -0...  
4  [-0.0046906215, 0.036938347, -0.028517464, 0.0...  
5  [-0.004665419, 0.036869112, -0.028484605, 0.01...  
6  [-0.032264102, -0.011765124, -0.04467337, 0.02...  
7  [-0.032264102, -0.011765124, -0.04467337, 0.02...  
8  [-0.032262914, -0.011764691, -0.044671725, 0.0...  
9  [-0.032264102, -0.011765124, -0.04467337, 0.02...

### Neural query によるニューラル検索の実行
[Neural query][neural] を使うことで、Search pipeline から埋め込みモデルを呼び出し、ユーザーのクエリデータを OpenSearch 側でベクトルデータに変換してから内部的にベクトル検索を実行することが可能となります。

仕組みは以下の通りです。model_id で指定した埋め込みモデルを使用し、query_text パラメーターに入力されたクエリテキストから生成したベクトルで knn query を実行しています。

<img src="./img/neural-search-query.png">

以下は question フィールドから生成された question_dense_embedding フィールドに対する Neural query の実行サンプルです。

[neural]: https://opensearch.org/docs/latest/query-dsl/specialized/neural/

In [28]:
%%time
index_name = "jsquad-neural-search"
query = "日本で梅雨がない場所は？"
payload = {
  "size": 10,
  "query": {
    "neural": {
      "question_embedding": {
        "query_text": query, 
        "model_id": opensearch_embedding_model_id,
        "k": 10
      }
    }
  },
  "_source" : False,
  "fields": ["question", "answers",  "context"]
}
# 検索 API を実行
response = opensearch_client.search(
    body = payload,
    index = index_name,
    filter_path = "hits.hits"
)

# 結果を表示
pd.json_normalize(response["hits"]["hits"])

CPU times: user 4.36 ms, sys: 43 μs, total: 4.4 ms
Wall time: 46.7 ms


_index          _id    _score  \
0  jsquad-neural-search  a10336p24q1  0.803610   
1  jsquad-neural-search  a10336p32q3  0.799850   
2  jsquad-neural-search  a10336p32q2  0.799580   
3  jsquad-neural-search   a10336p0q0  0.782569   
4  jsquad-neural-search  a10336p18q0  0.773138   
5  jsquad-neural-search  a10336p42q4  0.669261   
6  jsquad-neural-search  a10336p42q2  0.667886   
7  jsquad-neural-search  a10336p42q1  0.663655   
8  jsquad-neural-search  a10336p42q3  0.657064   
9  jsquad-neural-search  a10336p42q0  0.654869   

                              fields.question       fields.answers  \
0                         [梅雨が日本の中でない地域はどこか。]          [北海道, 東北地方]   
1                       [梅雨がないとされている都道府県はどこ？]                [北海道]   
2                     [気候学的には梅雨はないとされている場所は？]                [北海道]   
3                        [日本で梅雨がないのは北海道とどこか。]  [小笠原諸島, 小笠原諸島を除く日本]   
4                 [日本の地域で本格的な長雨に突入しない場所はどこか。]                [北海道]   
5                        [ほとんど雨が降らない梅雨を何という？]     [空梅雨, 空梅雨（からつゆ）]   
6                 [梅雨の期間中ほとんど雨が降らない場合をなんという？]     [空梅雨, 空梅雨（からつゆ）]   
7                  [梅雨の期間中ほとんど雨が降らない場合を何と呼ぶ？]     [空梅雨, 空梅雨（からつゆ）]   
8                        [ほとんど雨が降らない梅雨を何と呼ぶか]     [空梅雨, 空梅雨（からつゆ）]   
9  [梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことをなんというか？]     [空梅雨, 空梅雨（からつゆ）]   

                                      fields.context  
0  [梅雨 [SEP] 年によっては梅雨明けの時期が特定できなかったり、あるいは発表がされないこ...  
1  [梅雨 [SEP] 実際の気象としては北海道にも道南を中心に梅雨前線がかかることはあるが、平...  
2  [梅雨 [SEP] 実際の気象としては北海道にも道南を中心に梅雨前線がかかることはあるが、平...  
3  [梅雨 [SEP] 梅雨（つゆ、ばいう）は、北海道と小笠原諸島を除く日本、朝鮮半島南部、中国...  
4  [梅雨 [SEP] 次に梅雨前線は中国の江淮（長江流域・淮河流域）に北上する。6月下旬には華...  
5  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...  
6  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...  
7  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...  
8  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...  
9  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...

Neural query を使用することで、クライアントはテキストとモデル ID を渡すだけで、裏でベクトル検索が実行されるようになりました。

ただ、クライアントがモデル ID を検索の都度指定するのは不便に思えます。

そこで、先ほどの Search pipeline を使用して、クライアントがモデル ID を指定せずに Neural query を実行できるようにします。

In [29]:
%%time
index_name = "jsquad-neural-search"
query = "日本で梅雨がない場所は？"
payload = {
  "size": 10,
  "query": {
    "neural": {
      "question_embedding": {
        "query_text": query, 
        #model_id の指定は行わない
        "k": 10
      }
    }
  },
  "_source" : False,
  "fields": ["question", "answers",  "context"]
}
# 検索 API を実行
response = opensearch_client.search(
    body = payload,
    index = index_name,
    filter_path = "hits.hits",
    search_pipeline = search_pipeline_id #新たに追加
)

# 結果を表示
pd.json_normalize(response["hits"]["hits"])

CPU times: user 4.54 ms, sys: 66 μs, total: 4.6 ms
Wall time: 31.5 ms


_index          _id    _score  \
0  jsquad-neural-search  a10336p24q1  0.803610   
1  jsquad-neural-search  a10336p32q3  0.799850   
2  jsquad-neural-search  a10336p32q2  0.799580   
3  jsquad-neural-search   a10336p0q0  0.782569   
4  jsquad-neural-search  a10336p18q0  0.773138   
5  jsquad-neural-search  a10336p42q4  0.669261   
6  jsquad-neural-search  a10336p42q2  0.667886   
7  jsquad-neural-search  a10336p42q1  0.663655   
8  jsquad-neural-search  a10336p42q3  0.657064   
9  jsquad-neural-search  a10336p42q0  0.654869   

                              fields.question       fields.answers  \
0                         [梅雨が日本の中でない地域はどこか。]          [北海道, 東北地方]   
1                       [梅雨がないとされている都道府県はどこ？]                [北海道]   
2                     [気候学的には梅雨はないとされている場所は？]                [北海道]   
3                        [日本で梅雨がないのは北海道とどこか。]  [小笠原諸島, 小笠原諸島を除く日本]   
4                 [日本の地域で本格的な長雨に突入しない場所はどこか。]                [北海道]   
5                        [ほとんど雨が降らない梅雨を何という？]     [空梅雨, 空梅雨（からつゆ）]   
6                 [梅雨の期間中ほとんど雨が降らない場合をなんという？]     [空梅雨, 空梅雨（からつゆ）]   
7                  [梅雨の期間中ほとんど雨が降らない場合を何と呼ぶ？]     [空梅雨, 空梅雨（からつゆ）]   
8                        [ほとんど雨が降らない梅雨を何と呼ぶか]     [空梅雨, 空梅雨（からつゆ）]   
9  [梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことをなんというか？]     [空梅雨, 空梅雨（からつゆ）]   

                                      fields.context  
0  [梅雨 [SEP] 年によっては梅雨明けの時期が特定できなかったり、あるいは発表がされないこ...  
1  [梅雨 [SEP] 実際の気象としては北海道にも道南を中心に梅雨前線がかかることはあるが、平...  
2  [梅雨 [SEP] 実際の気象としては北海道にも道南を中心に梅雨前線がかかることはあるが、平...  
3  [梅雨 [SEP] 梅雨（つゆ、ばいう）は、北海道と小笠原諸島を除く日本、朝鮮半島南部、中国...  
4  [梅雨 [SEP] 次に梅雨前線は中国の江淮（長江流域・淮河流域）に北上する。6月下旬には華...  
5  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...  
6  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...  
7  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...  
8  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...  
9  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...

### 距離とスコアによるフィルタリング

[ベクトル検索の実装 (Amazon SageMaker 編)](./vector-search-with-sagemaker.ipynb) でも解説した、min_score および max_distance によるフィルタリングは Neural query でも利用可能です。

In [30]:
%%time
index_name = "jsquad-neural-search"
query = "日本で梅雨がない場所は？"
payload = {
  "size": 10,
  "query": {
    "neural": {
      "question_embedding": {
        "query_text": query, 
        #model_id の指定は行わない
        "min_score": 0.7
      }
    }
  },
  "_source" : False,
  "fields": ["question", "answers",  "context"]
}
# 検索 API を実行
response = opensearch_client.search(
    body = payload,
    index = index_name,
    filter_path = "hits.hits",
    search_pipeline = search_pipeline_id #新たに追加
)

# 結果を表示
pd.json_normalize(response["hits"]["hits"])

CPU times: user 4.56 ms, sys: 70 μs, total: 4.63 ms
Wall time: 23.6 ms


_index          _id    _score              fields.question  \
0  jsquad-neural-search  a10336p24q1  0.803610          [梅雨が日本の中でない地域はどこか。]   
1  jsquad-neural-search  a10336p32q3  0.799850        [梅雨がないとされている都道府県はどこ？]   
2  jsquad-neural-search  a10336p32q2  0.799580      [気候学的には梅雨はないとされている場所は？]   
3  jsquad-neural-search   a10336p0q0  0.782569         [日本で梅雨がないのは北海道とどこか。]   
4  jsquad-neural-search  a10336p18q0  0.773138  [日本の地域で本格的な長雨に突入しない場所はどこか。]   

        fields.answers                                     fields.context  
0          [北海道, 東北地方]  [梅雨 [SEP] 年によっては梅雨明けの時期が特定できなかったり、あるいは発表がされないこ...  
1                [北海道]  [梅雨 [SEP] 実際の気象としては北海道にも道南を中心に梅雨前線がかかることはあるが、平...  
2                [北海道]  [梅雨 [SEP] 実際の気象としては北海道にも道南を中心に梅雨前線がかかることはあるが、平...  
3  [小笠原諸島, 小笠原諸島を除く日本]  [梅雨 [SEP] 梅雨（つゆ、ばいう）は、北海道と小笠原諸島を除く日本、朝鮮半島南部、中国...  
4                [北海道]  [梅雨 [SEP] 次に梅雨前線は中国の江淮（長江流域・淮河流域）に北上する。6月下旬には華...

In [31]:
%%time
index_name = "jsquad-neural-search"
query = "日本で梅雨がない場所は？"
payload = {
  "size": 10,
  "query": {
    "neural": {
      "question_embedding": {
        "query_text": query, 
        #model_id の指定は行わない
        "max_distance": 0.3
      }
    }
  },
  "_source" : False,
  "fields": ["question", "answers",  "context"]
}
# 検索 API を実行
response = opensearch_client.search(
    body = payload,
    index = index_name,
    filter_path = "hits.hits",
    search_pipeline = search_pipeline_id #新たに追加
)

# 結果を表示
pd.json_normalize(response["hits"]["hits"])

CPU times: user 4.79 ms, sys: 116 μs, total: 4.9 ms
Wall time: 23.3 ms


_index          _id    _score              fields.question  \
0  jsquad-neural-search  a10336p24q1  0.803610          [梅雨が日本の中でない地域はどこか。]   
1  jsquad-neural-search  a10336p32q3  0.799850        [梅雨がないとされている都道府県はどこ？]   
2  jsquad-neural-search  a10336p32q2  0.799580      [気候学的には梅雨はないとされている場所は？]   
3  jsquad-neural-search   a10336p0q0  0.782569         [日本で梅雨がないのは北海道とどこか。]   
4  jsquad-neural-search  a10336p18q0  0.773138  [日本の地域で本格的な長雨に突入しない場所はどこか。]   

        fields.answers                                     fields.context  
0          [北海道, 東北地方]  [梅雨 [SEP] 年によっては梅雨明けの時期が特定できなかったり、あるいは発表がされないこ...  
1                [北海道]  [梅雨 [SEP] 実際の気象としては北海道にも道南を中心に梅雨前線がかかることはあるが、平...  
2                [北海道]  [梅雨 [SEP] 実際の気象としては北海道にも道南を中心に梅雨前線がかかることはあるが、平...  
3  [小笠原諸島, 小笠原諸島を除く日本]  [梅雨 [SEP] 梅雨（つゆ、ばいう）は、北海道と小笠原諸島を除く日本、朝鮮半島南部、中国...  
4                [北海道]  [梅雨 [SEP] 次に梅雨前線は中国の江淮（長江流域・淮河流域）に北上する。6月下旬には華...

### Appendix: ニューラル検索と従来のベクトル検索を組み合わせて使用する
本ラボでは、ニューラル検索を Ingest pipeline による登録データのテキスト(または画像)→ベクトル変換と、Search pipeline による検索クエリのベクトル変換を組み合わせて実装していきました。

Ingest pipeline と Search pipeline の併用は、実は必須ではありません。以下のようにどちらか一方のみを使用することもできます。
- データ登録は Ingest pipeline を通じて行うが、検索ではバックエンド側でベクトル生成を行ったうえで通常の knn query を用いる
- データ登録はバックエンド側でベクトル生成を行ったうえで、Ingest pipeline を使わず通常の bulk API で登録する。検索でのみ Search pipeline を介した neural query を用いる

例えば、以下のようなユースケースが考えられます。

- 初期構築時に極めて大量のベクトル登録を行う必要があるため、バッチ推論を使用して非同期でベクトルデータを生成し、通常の bulk API で登録を実施。初期構築後の部分更新、検索は Neural query で行う

以下のサンプルコードでは、[ベクトル検索の実装 (Amazon SageMaker 編)](./vector-search-with-sagemaker.ipynb) で作成した kNN 検索用のインデックスに対して Neural query を実行しています。

In [32]:
%%time
index_name = "jsquad-knn"
query = "日本で梅雨がない場所は？"
payload = {
  "size": 10,
  "query": {
    "neural": {
      "question_embedding": {
        "query_text": query, 
        "k": 10
      }
    }
  },
  "_source" : False,
  "fields": ["question", "answers",  "context"]
}
# 検索 API を実行
response = opensearch_client.search(
    body = payload,
    index = index_name,
    filter_path = "hits.hits",
    search_pipeline = search_pipeline_id
)

# 結果を表示
pd.json_normalize(response["hits"]["hits"])

CPU times: user 5.34 ms, sys: 225 μs, total: 5.56 ms
Wall time: 98.5 ms


_index          _id    _score  \
0  jsquad-knn  a10336p24q1  0.803372   
1  jsquad-knn  a10336p32q3  0.799814   
2  jsquad-knn  a10336p32q2  0.799580   
3  jsquad-knn   a10336p0q0  0.782644   
4  jsquad-knn  a10336p18q0  0.773163   
5  jsquad-knn  a10336p42q4  0.669258   
6  jsquad-knn  a10336p42q2  0.667771   
7  jsquad-knn  a10336p42q1  0.663624   
8  jsquad-knn  a10336p42q3  0.657195   
9  jsquad-knn  a10336p42q0  0.654841   

                              fields.question       fields.answers  \
0                         [梅雨が日本の中でない地域はどこか。]          [北海道, 東北地方]   
1                       [梅雨がないとされている都道府県はどこ？]                [北海道]   
2                     [気候学的には梅雨はないとされている場所は？]                [北海道]   
3                        [日本で梅雨がないのは北海道とどこか。]  [小笠原諸島, 小笠原諸島を除く日本]   
4                 [日本の地域で本格的な長雨に突入しない場所はどこか。]                [北海道]   
5                        [ほとんど雨が降らない梅雨を何という？]     [空梅雨, 空梅雨（からつゆ）]   
6                 [梅雨の期間中ほとんど雨が降らない場合をなんという？]     [空梅雨, 空梅雨（からつゆ）]   
7                  [梅雨の期間中ほとんど雨が降らない場合を何と呼ぶ？]     [空梅雨, 空梅雨（からつゆ）]   
8                        [ほとんど雨が降らない梅雨を何と呼ぶか]     [空梅雨, 空梅雨（からつゆ）]   
9  [梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことをなんというか？]     [空梅雨, 空梅雨（からつゆ）]   

                                      fields.context  
0  [梅雨 [SEP] 年によっては梅雨明けの時期が特定できなかったり、あるいは発表がされないこ...  
1  [梅雨 [SEP] 実際の気象としては北海道にも道南を中心に梅雨前線がかかることはあるが、平...  
2  [梅雨 [SEP] 実際の気象としては北海道にも道南を中心に梅雨前線がかかることはあるが、平...  
3  [梅雨 [SEP] 梅雨（つゆ、ばいう）は、北海道と小笠原諸島を除く日本、朝鮮半島南部、中国...  
4  [梅雨 [SEP] 次に梅雨前線は中国の江淮（長江流域・淮河流域）に北上する。6月下旬には華...  
5  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...  
6  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...  
7  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...  
8  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...  
9  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...

また、本ラボで構築した Neural search 用のインデックスに対して、knn query を実行することもできます。以下はサンプルコードです。

In [33]:
index_name = "jsquad-neural-search"

query = "日本で梅雨がない場所は？"

def text_to_embedding(text, region_name, embedding_endpoint_name):
    payload = {
        "inputs": [
            query
        ]
    }
    body = bytes(json.dumps(payload), 'utf-8')
    sagemaker_runtime_client = boto3.client("sagemaker-runtime", region_name=region_name)
    response = sagemaker_runtime_client.invoke_endpoint(
        EndpointName=embedding_endpoint_name,
        ContentType="application/json",
        Accept="application/json",
        Body=body
    )
    embeddings = eval(response['Body'].read().decode('utf-8'))
    return embeddings[0]

vector = text_to_embedding(text=query, region_name=sagemaker_region, embedding_endpoint_name=embedding_endpoint_name)
k = 10

payload = {
  "query": {
    "knn": {
      "question_embedding": {
        "vector": vector,
        "k": k
      }
    }
  },
  "_source": False,
  "fields": ["question", "answers", "context"],
  "size": k
}

response = opensearch_client.search(
    index=index_name,
    body=payload
)

pd.json_normalize(response["hits"]["hits"])


_index          _id    _score  \
0  jsquad-neural-search  a10336p24q1  0.803610   
1  jsquad-neural-search  a10336p32q3  0.799850   
2  jsquad-neural-search  a10336p32q2  0.799580   
3  jsquad-neural-search   a10336p0q0  0.782569   
4  jsquad-neural-search  a10336p18q0  0.773138   
5  jsquad-neural-search  a10336p42q4  0.669261   
6  jsquad-neural-search  a10336p42q2  0.667886   
7  jsquad-neural-search  a10336p42q1  0.663655   
8  jsquad-neural-search  a10336p42q3  0.657064   
9  jsquad-neural-search  a10336p42q0  0.654869   

                              fields.question       fields.answers  \
0                         [梅雨が日本の中でない地域はどこか。]          [北海道, 東北地方]   
1                       [梅雨がないとされている都道府県はどこ？]                [北海道]   
2                     [気候学的には梅雨はないとされている場所は？]                [北海道]   
3                        [日本で梅雨がないのは北海道とどこか。]  [小笠原諸島, 小笠原諸島を除く日本]   
4                 [日本の地域で本格的な長雨に突入しない場所はどこか。]                [北海道]   
5                        [ほとんど雨が降らない梅雨を何という？]     [空梅雨, 空梅雨（からつゆ）]   
6                 [梅雨の期間中ほとんど雨が降らない場合をなんという？]     [空梅雨, 空梅雨（からつゆ）]   
7                  [梅雨の期間中ほとんど雨が降らない場合を何と呼ぶ？]     [空梅雨, 空梅雨（からつゆ）]   
8                        [ほとんど雨が降らない梅雨を何と呼ぶか]     [空梅雨, 空梅雨（からつゆ）]   
9  [梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことをなんというか？]     [空梅雨, 空梅雨（からつゆ）]   

                                      fields.context  
0  [梅雨 [SEP] 年によっては梅雨明けの時期が特定できなかったり、あるいは発表がされないこ...  
1  [梅雨 [SEP] 実際の気象としては北海道にも道南を中心に梅雨前線がかかることはあるが、平...  
2  [梅雨 [SEP] 実際の気象としては北海道にも道南を中心に梅雨前線がかかることはあるが、平...  
3  [梅雨 [SEP] 梅雨（つゆ、ばいう）は、北海道と小笠原諸島を除く日本、朝鮮半島南部、中国...  
4  [梅雨 [SEP] 次に梅雨前線は中国の江淮（長江流域・淮河流域）に北上する。6月下旬には華...  
5  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...  
6  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...  
7  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...  
8  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...  
9  [梅雨 [SEP] 梅雨の期間中ほとんど雨が降らない場合がある。このような梅雨のことを空梅雨...

## まとめ

ラボを通して、OpenSearch 側でベクトル変換を行うニューラル検索の機能を確認できました。時間がある方は、続いて以下のラボも実施してみましょう。

- [スパース検索の実装 (Amazon SageMaker 編)](../sparse-search/sparse-search-with-sagemaker.ipynb)

## 後片付け

### データセット削除
ダウンロードしたデータセットを削除します。./dataset ディレクトリ配下に何もない場合は、./dataset ディレクトリも合わせて削除します。

In [34]:
%rm -rf {dataset_dir}

In [35]:
%rmdir ./dataset